Instituto Tecnológico de Costa Rica<br>
Ingeniería en Computación<br>
Bases de Datos 2<br>
Profesor: Kenneth Obando Rodríguez<br>
Estudiantes:<br>
Ian Coto Soto - 2021121435<br>
Brandon Calderón Cubero - 2021019600

In [2]:
from pymongo import MongoClient

client = MongoClient('localhost', 27017, username='root', password='example')

db = client['posts']
posts_collection = db['posts']
posts_collection.drop()

In [3]:
from itertools import islice
import json
from datetime import datetime
from tqdm import tqdm

# Añadir datos a la colección
with open ('data.jsonl', 'r') as file:
    for line in tqdm(file): # 1435 en total
        data = json.loads(line)
        data['post']['timestamp'] = datetime.fromisoformat(data['post']['timestamp'])
        for comment in data['comments']:
            comment['comment']['timestamp'] = datetime.fromisoformat(comment['comment']['timestamp'])
        posts_collection.insert_one(data)

13it [00:00, 129.00it/s]

1698it [00:05, 320.93it/s]


In [142]:
# Limpiar datos
posts_collection.delete_many({})

DeleteResult({'n': 1440, 'ok': 1.0}, acknowledged=True)

Ejemplo JSON en formato

In [ ]:
{
  "user": "Lindsay Thornton",
  "user_email": "alexanderwheeler@example.org",
  "user_age": 28,
  "post": {
    "title": "Random title for Lindsay Thornton",
    "content": "Random content for Lindsay Thornton Pressure employee by above law its not. Way open a such whether cut. Election scientist money role wait serious lot. Sort control man go really quality region.",
    "timestamp": "2001-12-22T13:33:57.415698"
  },
  "comments": [
    {
      "user": "Kristi Cooley",
      "user_email": "claytoncody@example.org",
      "user_age": 39,
      "comment": {
        "text": "Random text Capital measure anyone provide PM instead few.\nThan hotel study especially once. Performance eye right president minute admit treat. Before mind would stay role garden.",
        "timestamp": "1998-07-21T12:59:07.588567"
      }
    }
  ]
}

1. Operaciones CRUD básicas (Crear, Leer, Actualizar, Eliminar)

In [141]:
# 1. Insertar 5 nuevos documentos de usuario con datos únicos.
import random

from faker import Faker

# Create an instance of the Faker class
fake = Faker()

# Create posts
def generateUsers(quantity):
    users = []
    for _ in range(quantity):
        user = {}
        user["name"] = fake.name()
        user["email"] = fake.email()
        user["age"] = random.randint(18, 60)
        users.append(user)
    return users

def generatePosts(quantityUsers, quantityPostsPerUser):
    data = []
    users = generateUsers(quantityUsers)
    for user in users:
        for _ in range(quantityPostsPerUser):
            post = {}
            post["user"] = user["name"]
            post["user_email"] = user["email"]
            post["user_age"] = user["age"]
            post["post"] = {}
            post["post"]["title"] = f'Random title for {user["name"]}'
            post["post"]["content"] = f'Random content for {user["name"]} {fake.text()}'
            post["post"]["timestamp"] = fake.date_time().isoformat()
            num_comments = random.randint(0, 5)
            post["comments"] = []
            for _ in range(num_comments):
                comment = {}
                comment["user"] = random.choice(users)["name"]
                comment["user_email"] = random.choice(users)["email"]
                comment["user_age"] = random.choice(users)["age"]
                comment["comment"] = {}
                comment["comment"]["text"] = f"Random text {fake.text()}"
                comment["comment"]["timestamp"] = fake.date_time().isoformat()
                post["comments"].append(comment)
            data.append(post)
    return data

# Crea 5 nuevos documentos de usuario con datos únicos
def createDocuments(quantityUsers, quantityPostsPerUser):
    datas = generatePosts(quantityUsers, quantityPostsPerUser)
    print(datas)
    for data in datas:
        data['post']['timestamp'] = datetime.fromisoformat(data['post']['timestamp'])
        for comment in data['comments']:
            comment['comment']['timestamp'] = datetime.fromisoformat(comment['comment']['timestamp'])
    return datas
    
db.posts.insert_many(createDocuments(5, 1), ordered=True)

[{'user': 'Maria Robles', 'user_email': 'barbarawilliams@example.net', 'user_age': 20, 'post': {'title': 'Random title for Maria Robles', 'content': 'Random content for Maria Robles Score whole end summer sea threat western. Way everybody article can break onto. Article away candidate pull agency organization vote.', 'timestamp': '2015-12-22T00:54:40'}, 'comments': [{'user': 'Maria Robles', 'user_email': 'angelamiller@example.com', 'user_age': 20, 'comment': {'text': 'Random text Away heavy but kid size night eye time. Improve blood maintain ok seek idea. Little section political huge spend.\nPretty natural foot watch. Phone drive pretty nothing deep wife.', 'timestamp': '1974-10-03T03:43:32'}}, {'user': 'Maria Robles', 'user_email': 'heatherspencer@example.net', 'user_age': 60, 'comment': {'text': 'Random text Less peace finally two despite television. Fire live bar two away. First recognize here lose military bed keep.', 'timestamp': '2023-10-30T03:54:47'}}, {'user': 'Rhonda Delgado'

InsertManyResult([ObjectId('65f1fcab4e73146462f55664'), ObjectId('65f1fcab4e73146462f55665'), ObjectId('65f1fcab4e73146462f55666'), ObjectId('65f1fcab4e73146462f55667'), ObjectId('65f1fcab4e73146462f55668')], acknowledged=True)

In [144]:
# 2. Buscar todos los usuarios con edad mayor a 25.
db.posts.distinct('user', {'user_age': {'$gt': 25}})

['Amanda Johnson',
 'Andrea Kennedy',
 'Beth Mendez',
 'Catherine Rios',
 'Christopher Jenkins',
 'Debra Smith DDS',
 'Gary Best',
 'Jacob Carroll',
 'Jeffrey Perez',
 'John Griffin',
 'Jon Rodriguez',
 'Joshua Murray',
 'Kayla Hill',
 'Lindsay Thornton',
 'Margaret Flores',
 'Michael Carr',
 'Michael Smith',
 'Mrs. Christine Sawyer',
 'Richard Bonilla',
 'Robert Wood',
 'Timothy Gallegos',
 'Todd Park',
 'Travis Nicholson',
 'Zachary King']

In [145]:
# 3. Buscar un usuario por dirección de correo electrónico.
db.posts.distinct('user', {'user_email': 'tmartin@example.org'}) # Actualizar correo si es necesario

['Joann Bowen']

In [150]:
# 4. Actualizar el contenido de la publicación de un usuario específico
from bson import ObjectId

print("Ids:", list(db.posts.find({}, {'_id':1})))
print("Pre-update:", list(db.posts.find({'_id': ObjectId('65f1fcb64e73146462f55669')}))) # Hay que actualizar el ObjectId
db.posts.update_one(
    {'_id': ObjectId('65f1fcb64e73146462f55669')}, 
    {'$set': 
        {'post': 
            {'title': 'New title', 
             'content': 'New content', 
             'timestamp': datetime.fromisoformat('2021-12-22T13:33:57.415698')
             }
        }
    }
)
print("Post-update:", list(db.posts.find({'_id': ObjectId('65f1fcb64e73146462f55669')})))

Ids: [{'_id': ObjectId('65f1fcb64e73146462f55669')}, {'_id': ObjectId('65f1fcb64e73146462f5566a')}, {'_id': ObjectId('65f1fcb64e73146462f5566b')}, {'_id': ObjectId('65f1fcb64e73146462f5566c')}, {'_id': ObjectId('65f1fcb64e73146462f5566d')}, {'_id': ObjectId('65f1fcb64e73146462f5566e')}, {'_id': ObjectId('65f1fcb64e73146462f5566f')}, {'_id': ObjectId('65f1fcb64e73146462f55670')}, {'_id': ObjectId('65f1fcb64e73146462f55671')}, {'_id': ObjectId('65f1fcb64e73146462f55672')}, {'_id': ObjectId('65f1fcb64e73146462f55673')}, {'_id': ObjectId('65f1fcb64e73146462f55674')}, {'_id': ObjectId('65f1fcb64e73146462f55675')}, {'_id': ObjectId('65f1fcb64e73146462f55676')}, {'_id': ObjectId('65f1fcb64e73146462f55677')}, {'_id': ObjectId('65f1fcb64e73146462f55678')}, {'_id': ObjectId('65f1fcb64e73146462f55679')}, {'_id': ObjectId('65f1fcb64e73146462f5567a')}, {'_id': ObjectId('65f1fcb64e73146462f5567b')}, {'_id': ObjectId('65f1fcb64e73146462f5567c')}, {'_id': ObjectId('65f1fcb64e73146462f5567d')}, {'_id':

In [4]:
# 5. Eliminar un documento de usuario y todos sus comentarios asociados.
db.posts.delete_many({"user": 'Lindsay Thornton'})
db.posts.update_many({}, {"$pull": {"post.comments": {'user':'Linsay Thornton' }}})

UpdateResult({'n': 1698, 'nModified': 0, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

2. Consultas con operadores

In [5]:
# 1. Buscar todos los usuarios cuyo nombre de usuario contenga la palabra S̈mith.̈ (Expresiones regulares)
list(db.posts.find({ 'user': { '$regex': 'Smith'} }))

[{'_id': ObjectId('65f26c140f6b455557036582'),
  'user': 'James Smith',
  'user_email': 'garrisonmartin@example.net',
  'user_age': 50,
  'post': {'title': 'Random title for James Smith',
   'content': 'Random content for James Smith Western forward decade trip boy bad laugh message. Often wind foot place. Become window top garden view be turn young. Turn certain space man quite.',
   'timestamp': datetime.datetime(1971, 8, 30, 8, 32, 52)},
  'comments': [{'user': 'Margaret York',
    'user_email': 'ypowell@example.com',
    'user_age': 30,
    'comment': {'text': 'Random text Size wrong research black international write. Hand on top reduce environment.\nSuccess against minute whole. Travel before trial how where until off.',
     'timestamp': datetime.datetime(2002, 12, 14, 13, 57, 9)}},
   {'user': 'Cynthia Park',
    'user_email': 'gramos@example.com',
    'user_age': 38,
    'comment': {'text': 'Random text Population thank new. Individual such four allow high western me view. Her

In [6]:
# 2. Buscar publicaciones creadas después de una fecha específica (por ejemplo, 2000-01-01).
timestamp = datetime(2000, 1, 1)
list(db.posts.find({'post.timestamp': {'$gt': timestamp}}))

[{'_id': ObjectId('65f26c110f6b4555570360b7'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Range degree last song job before. Drive could local them window her determine.',
   'timestamp': datetime.datetime(2004, 5, 4, 11, 51, 14)},
  'comments': [{'user': 'William Stevens',
    'user_email': 'brownbrianna@example.org',
    'user_age': 38,
    'comment': {'text': 'Random text Foreign inside plant radio institution special shoulder. Police color ever check sometimes.\nDetail seven the pick. Pressure heavy brother person wear themselves.',
     'timestamp': datetime.datetime(2009, 11, 15, 0, 4, 44)}}]},
 {'_id': ObjectId('65f26c110f6b4555570360b8'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Character we

In [7]:
# 3. Buscar usuarios que aún no han publicado ningún comentario.
list(db.posts.find({'$or': [{'comments': {'$exists': False}},{'comments': {'$size': 0}}]}))

[{'_id': ObjectId('65f26c110f6b4555570360b8'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Character well I my officer. Development recent day bad by.\nPosition grow question operation father camera need I.\nAny too contain worry. Stuff one see start wind entire.',
   'timestamp': datetime.datetime(2007, 12, 23, 13, 19, 15)},
  'comments': []},
 {'_id': ObjectId('65f26c110f6b4555570360c0'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Close full appear decide.\nAmerican something actually half. Organization mouth relationship move up true.',
   'timestamp': datetime.datetime(1975, 12, 14, 21, 43, 46)},
  'comments': []},
 {'_id': ObjectId('65f26c110f6b4555570360ce'),
  'user': 'Angela Collins',
  'user_e

In [8]:
# 4. Encontrar la edad promedio de todos los usuarios.
list(db.posts.aggregate([{'$group': {'_id': None, 'edadPromedio': {'$avg': '$user_age'}}}]))

[{'_id': None, 'edadPromedio': 42.975265017667844}]

In [151]:
#5. Buscar documentos donde la longitud del contenido de la publicación sea superior a 100 caracteres.
list(db.posts.find(
                    {"$expr":
                        {"$gt": [{"$strLenCP": "$post.content"}, 100]}
                    }
    )
)

[{'_id': ObjectId('65f1fcb64e73146462f5566a'),
  'user': 'Lindsay Thornton',
  'user_email': 'alexanderwheeler@example.org',
  'user_age': 28,
  'post': {'title': 'Random title for Lindsay Thornton',
   'content': 'Random content for Lindsay Thornton Career real suggest consider present industry. Else pattern leader. Economy course change yes same. Bill record my rise herself spend door.',
   'timestamp': datetime.datetime(1992, 5, 3, 2, 1, 29, 34000)},
  'comments': [{'user': 'Beth Mendez',
    'user_email': 'carrie93@example.com',
    'user_age': 49,
    'comment': {'text': 'Random text Foot that early level prevent general century. First including artist everyone discussion.\nCapital fear deep.',
     'timestamp': datetime.datetime(1993, 5, 18, 10, 31, 49, 908000)}},
   {'user': 'Michael Smith',
    'user_email': 'reneeterry@example.org',
    'user_age': 28,
    'comment': {'text': 'Random text Establish represent wear. Although everything name interest provide network.\nForm action

3. Operadores lógicos y proyección

In [9]:
# 1. Buscar usuarios que tengan más de 20 años pero menos de 30. (Combinar operadores)
list(db.posts.find({'user_age': {'$gt': 20, '$lt': 30}}))


[{'_id': ObjectId('65f26c110f6b455557036109'),
  'user': 'Andre Mccarthy',
  'user_email': 'brownbrianna@example.org',
  'user_age': 25,
  'post': {'title': 'Random title for Andre Mccarthy',
   'content': 'Random content for Andre Mccarthy Full win writer agent party their. Without know another chair administration. Middle policy quickly box.',
   'timestamp': datetime.datetime(1982, 10, 24, 20, 2, 47)},
  'comments': [{'user': 'Benjamin Cabrera',
    'user_email': 'burnettsharon@example.org',
    'user_age': 33,
    'comment': {'text': 'Random text World degree reveal also knowledge Congress. Individual itself economic hand sure power election open.',
     'timestamp': datetime.datetime(1997, 2, 1, 14, 12, 53)}}]},
 {'_id': ObjectId('65f26c110f6b45555703610a'),
  'user': 'Andre Mccarthy',
  'user_email': 'brownbrianna@example.org',
  'user_age': 25,
  'post': {'title': 'Random title for Andre Mccarthy',
   'content': 'Random content for Andre Mccarthy Some east five. Position above e

In [152]:
# 2. Recuperar solo el nombre de usuario y la edad del usuario de todos los documentos. (Proyección)
list(db.posts.find({}, {'user': 1, 'user_age': 1, '_id': 0}))

[{'user': 'Lindsay Thornton', 'user_age': 28},
 {'user': 'Lindsay Thornton', 'user_age': 28},
 {'user': 'Lindsay Thornton', 'user_age': 28},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Joann Bowen', 'user_age': 19},
 {'user': 'Mrs. Christine Sawyer', 'user_age': 37},
 {'user': 'Mrs. Christine Sawyer', 'user_age': 37},
 {'user': 'Mrs. Christine Sawyer', 'user_age': 37},
 {'user': 'Mrs. Christine Sawyer', 'user_age': 37},
 {'user': 'Mrs. Christine Sawyer', 'user_age': 37},
 {'user': 'Kayla Hill', 'user_age': 29},
 {'user': 'Kayla Hill', 'user_age': 29},
 {'user': 'Ka

In [10]:
# 3. Buscar todas las publicaciones y excluir el campo ”comentarios”.
list(db.posts.find({}, {'comments': 0}))

[{'_id': ObjectId('65f26c100f6b4555570360b6'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Year huge interest fear.\nCharacter including time member evidence situation.\nHope nation realize arm. Federal may real management. Not sure reduce.',
   'timestamp': datetime.datetime(1996, 3, 20, 14, 21, 26)}},
 {'_id': ObjectId('65f26c110f6b4555570360b7'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Angela Collins',
   'content': 'Random content for Angela Collins Range degree last song job before. Drive could local them window her determine.',
   'timestamp': datetime.datetime(2004, 5, 4, 11, 51, 14)}},
 {'_id': ObjectId('65f26c110f6b4555570360b8'),
  'user': 'Angela Collins',
  'user_email': 'zgreen@example.org',
  'user_age': 33,
  'post': {'title': 'Random title for Ange

In [153]:
# 4. Buscar usuarios con al menos un comentario en su matriz ”comentarios”.
list(db.posts.find(
                    {"$expr":
                        {"$gt": [{"$size": "$comments"}, 0]}
                    },
                    {'user': 1, '_id': 0}
    )
)

[{'user': 'Lindsay Thornton'},
 {'user': 'Lindsay Thornton'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Mrs. Christine Sawyer'},
 {'user': 'Mrs. Christine Sawyer'},
 {'user': 'Mrs. Christine Sawyer'},
 {'user': 'Mrs. Christine Sawyer'},
 {'user': 'Mrs. Christine Sawyer'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},
 {'user': 'Kayla Hill'},

In [11]:
# 5. Buscar comentarios publicados por usuarios mayores de 40 años. (Consultas anidadas)
list(db.posts.aggregate([
    {"$unwind": "$comments"},{"$replaceRoot": {"newRoot": "$comments"}},
    {"$match": {"user_age": {"$gt": 40}}}]))

[{'user': 'Daniel Christensen',
  'user_email': 'bnguyen@example.org',
  'user_age': 60,
  'comment': {'text': 'Random text Interest long work else and. Bit sound sound travel hold science firm nothing. Partner free account light skin experience idea.\nMe worry around task should natural energy.',
   'timestamp': datetime.datetime(2006, 10, 26, 6, 32, 4)}},
 {'user': 'Robert Brown',
  'user_email': 'burnettsharon@example.org',
  'user_age': 58,
  'comment': {'text': 'Random text Network once five. Result son guy still contain true nothing skin.\nVarious sit yeah knowledge as.',
   'timestamp': datetime.datetime(1999, 11, 10, 15, 22, 6)}},
 {'user': 'Daniel Christensen',
  'user_email': 'ldillon@example.com',
  'user_age': 54,
  'comment': {'text': 'Random text City add ground leg media. Also task develop ever public month.\nStrategy law thought woman see. Finish blue condition stuff fear.',
   'timestamp': datetime.datetime(2012, 11, 13, 18, 59, 38)}},
 {'user': 'Justin Tate',
  'user_

4. Ordenar y limitar

In [154]:
# 1. Ordenar todos los usuarios por edad en orden descendente.
list(db.posts.aggregate([
        {'$group': {'_id': '$user', 'user_age': {'$first': '$user_age'}}},
        {'$project': {'_id': 0, 'user': '$_id', 'user_age': 1}},
        {'$sort': {'user_age': -1}}
    ])
)

[{'user_age': 53, 'user': 'Richard Bonilla'},
 {'user_age': 51, 'user': 'Jacob Carroll'},
 {'user_age': 50, 'user': 'Robert Wood'},
 {'user_age': 49, 'user': 'Timothy Gallegos'},
 {'user_age': 48, 'user': 'Gary Best'},
 {'user_age': 46, 'user': 'Michael Carr'},
 {'user_age': 46, 'user': 'Zachary King'},
 {'user_age': 44, 'user': 'Beth Mendez'},
 {'user_age': 42, 'user': 'Margaret Flores'},
 {'user_age': 42, 'user': 'Travis Nicholson'},
 {'user_age': 41, 'user': 'Todd Park'},
 {'user_age': 40, 'user': 'Christopher Jenkins'},
 {'user_age': 39, 'user': 'Jeffrey Perez'},
 {'user_age': 37, 'user': 'Andrea Kennedy'},
 {'user_age': 37, 'user': 'Mrs. Christine Sawyer'},
 {'user_age': 34, 'user': 'John Griffin'},
 {'user_age': 33, 'user': 'Jon Rodriguez'},
 {'user_age': 33, 'user': 'Catherine Rios'},
 {'user_age': 32, 'user': 'Joshua Murray'},
 {'user_age': 30, 'user': 'Amanda Johnson'},
 {'user_age': 29, 'user': 'Kayla Hill'},
 {'user_age': 28, 'user': 'Lindsay Thornton'},
 {'user_age': 28, 'u

In [12]:
# 2. Buscar los 3 usuarios principales con las publicaciones más recientes (en función de la marca de tiempo).
list(db.posts.aggregate([
    {'$sort': {'post.timestamp': -1}},{'$group': {'_id': '$user','latestPost': {'$first': '$post.timestamp'}}},{'$sort': {'latestPost': -1}},{'$limit': 3},{'$project': {'_id': 1}}]))

[{'_id': 'John Neal'}, {'_id': 'Billy Neal'}, {'_id': 'Victor Mclaughlin'}]

In [155]:
# 3. Omitir los primeros 5 resultados y recuperar los próximos 10 usuarios
list(db.posts.find({}, {'_id':0, 'user':1}).skip(5).limit(10))

[{'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'},
 {'user': 'Joann Bowen'}]

5. Marco de agregación

In [13]:
# 1. Utilizar el pipeline de agregación para calcular el número total de usuarios.
list(db.posts.aggregate([{'$group': { '_id': None, 'totalUsuarios': {'$sum': 1} }}]))

[{'_id': None, 'totalUsuarios': 1698}]

In [159]:
# 2. Encontrar al usuario con el contenido de publicación más largo (en función del número de caracteres).
list(db.posts.aggregate([
    {'$project': {'_id': 0, 'user': 1, 'largo_publicacion': {'$strLenCP': '$post.content'}}},
    {'$sort': {'largo_publicacion': -1}},
    {'$limit': 1}
]))

[{'user': 'Christopher Jenkins', 'largo_publicacion': 238}]

In [14]:
# 3. Agrupar a los usuarios por edad y contar la cantidad de usuarios en cada grupo de edad.
list(db.posts.aggregate([{'$group': {'_id': '$user_age', 'cantidadUsuarios': {'$sum': 1} }},{'$sort': {'_id': 1}}]))

[{'_id': 18, 'cantidadUsuarios': 15},
 {'_id': 21, 'cantidadUsuarios': 32},
 {'_id': 22, 'cantidadUsuarios': 169},
 {'_id': 25, 'cantidadUsuarios': 124},
 {'_id': 30, 'cantidadUsuarios': 66},
 {'_id': 33, 'cantidadUsuarios': 83},
 {'_id': 36, 'cantidadUsuarios': 85},
 {'_id': 38, 'cantidadUsuarios': 6},
 {'_id': 42, 'cantidadUsuarios': 80},
 {'_id': 43, 'cantidadUsuarios': 74},
 {'_id': 45, 'cantidadUsuarios': 74},
 {'_id': 46, 'cantidadUsuarios': 144},
 {'_id': 48, 'cantidadUsuarios': 146},
 {'_id': 50, 'cantidadUsuarios': 87},
 {'_id': 51, 'cantidadUsuarios': 69},
 {'_id': 53, 'cantidadUsuarios': 35},
 {'_id': 54, 'cantidadUsuarios': 53},
 {'_id': 58, 'cantidadUsuarios': 97},
 {'_id': 59, 'cantidadUsuarios': 51},
 {'_id': 60, 'cantidadUsuarios': 208}]

In [161]:
# 4. Calcular la longitud promedio de los comentarios en todos los comentarios.
# Promedio de todos los comentarios de todas las publicaciones
print("Todos:\n", list(db.posts.aggregate([
    {'$unwind': '$comments'},
    {'$match': {'comments.comment.text': {'$exists': True}}},
    {'$group': {'_id': None, 'largo_promedio': {'$avg': {'$strLenCP': '$comments.comment.text'}}}},
    {'$project': {'_id': 0, 'largo_promedio': 1}}
])))

# Promedio de todos los comentarios de cada publicación
print("Por publicación:\n", list(db.posts.aggregate([
    {'$unwind': '$comments'},
    {'$match': {'comments.comment.text': {'$exists': True}}},
    {'$group': {'_id': '$_id', 'largo_promedio': {'$avg': {'$strLenCP': '$comments.comment.text'}}}},
    {'$project': {'_id': 1, 'largo_promedio': 1}}
])))

Todos:
 [{'largo_promedio': 159.29229092890222}]
Por publicación:
 [{'_id': ObjectId('65f1fcb74e73146462f559e3'), 'largo_promedio': 170.66666666666666}, {'_id': ObjectId('65f1fcb74e73146462f55a54'), 'largo_promedio': 163.66666666666666}, {'_id': ObjectId('65f1fcb74e73146462f55bc0'), 'largo_promedio': 156.0}, {'_id': ObjectId('65f1fcb74e73146462f55bb0'), 'largo_promedio': 164.5}, {'_id': ObjectId('65f1fcb74e73146462f55921'), 'largo_promedio': 125.0}, {'_id': ObjectId('65f1fcb74e73146462f559d1'), 'largo_promedio': 171.5}, {'_id': ObjectId('65f1fcb74e73146462f55b39'), 'largo_promedio': 174.0}, {'_id': ObjectId('65f1fcb74e73146462f55b56'), 'largo_promedio': 182.0}, {'_id': ObjectId('65f1fcb64e73146462f5570b'), 'largo_promedio': 167.0}, {'_id': ObjectId('65f1fcb64e73146462f55766'), 'largo_promedio': 164.0}, {'_id': ObjectId('65f1fcb74e73146462f557e4'), 'largo_promedio': 158.0}, {'_id': ObjectId('65f1fcb74e73146462f557d5'), 'largo_promedio': 181.8}, {'_id': ObjectId('65f1fcb74e73146462f55bd6

In [16]:
# 5. Cambiar la forma como se presentan los datos, de tal forma que cada usuario tenga la lista de todos
# los posts asociados a él. No se deben agregar el detalle de los comentarios, solo un nuevo campo con
# el total de comentarios.
list(db.posts.aggregate([
    {'$group': {'_id': '$user','posts': {'$push': {'title': '$post.title','content': '$post.content','timestamp': '$post.timestamp','totalComments': {'$size': '$comments'}}}}},
    {'$project': {'user': '$user','_id': 1, 'posts': 1 }}]))

[{'_id': 'Andre Mccarthy',
  'posts': [{'title': 'Random title for Andre Mccarthy',
    'content': 'Random content for Andre Mccarthy Full win writer agent party their. Without know another chair administration. Middle policy quickly box.',
    'timestamp': datetime.datetime(1982, 10, 24, 20, 2, 47),
    'totalComments': 1},
   {'title': 'Random title for Andre Mccarthy',
    'content': 'Random content for Andre Mccarthy Some east five. Position above eye main people into economy. Play maybe charge media situation business.',
    'timestamp': datetime.datetime(1983, 10, 19, 22, 18, 36),
    'totalComments': 3},
   {'title': 'Random title for Andre Mccarthy',
    'content': 'Random content for Andre Mccarthy Their minute condition deep. Top expert inside.\nSign resource fish high citizen improve. Charge so major write write air message probably.\nBetter body stock rich president.',
    'timestamp': datetime.datetime(1985, 1, 3, 20, 56, 11),
    'totalComments': 2},
   {'title': 'Random 

6. Actualización y eliminación con operadores

In [162]:
# 1. Incrementar la edad de todos los usuarios en 1.
db.posts.update_many({}, {'$inc': {'user_age': 1}})

UpdateResult({'n': 1435, 'nModified': 1435, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [19]:
# 2. Establecer el campo ”contenido” de una publicación específica en una cadena vacía.
from bson.objectid import ObjectId
db.posts.update_one({'_id': ObjectId('65f26c100f6b4555570360b6')}, {'$set': {'post.content': ''}})

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [166]:
# 3. Eliminar todos los comentarios de la publicación de un usuario.
from bson import ObjectId

print("Ids:", list(db.posts.find({}, {'_id':1})))
print("Pre-update:", list(db.posts.find({'_id': ObjectId('65f1fcb64e73146462f55669')}))) # Actualizar ObjectId
db.posts.update_one(
                {'_id': ObjectId('65f1fcb64e73146462f55669')}, # Actualizar ObjectId
                {'$set': {'comments': []}}
)
print("Post-update:", list(db.posts.find({'_id': ObjectId('65f1fcb64e73146462f55669')})))

Ids: [{'_id': ObjectId('65f1fcb64e73146462f55669')}, {'_id': ObjectId('65f1fcb64e73146462f5566a')}, {'_id': ObjectId('65f1fcb64e73146462f5566b')}, {'_id': ObjectId('65f1fcb64e73146462f5566c')}, {'_id': ObjectId('65f1fcb64e73146462f5566d')}, {'_id': ObjectId('65f1fcb64e73146462f5566e')}, {'_id': ObjectId('65f1fcb64e73146462f5566f')}, {'_id': ObjectId('65f1fcb64e73146462f55670')}, {'_id': ObjectId('65f1fcb64e73146462f55671')}, {'_id': ObjectId('65f1fcb64e73146462f55672')}, {'_id': ObjectId('65f1fcb64e73146462f55673')}, {'_id': ObjectId('65f1fcb64e73146462f55674')}, {'_id': ObjectId('65f1fcb64e73146462f55675')}, {'_id': ObjectId('65f1fcb64e73146462f55676')}, {'_id': ObjectId('65f1fcb64e73146462f55677')}, {'_id': ObjectId('65f1fcb64e73146462f55678')}, {'_id': ObjectId('65f1fcb64e73146462f55679')}, {'_id': ObjectId('65f1fcb64e73146462f5567a')}, {'_id': ObjectId('65f1fcb64e73146462f5567b')}, {'_id': ObjectId('65f1fcb64e73146462f5567c')}, {'_id': ObjectId('65f1fcb64e73146462f5567d')}, {'_id':

In [20]:
# 4. Eliminar todos los usuarios con direcciones de correo electrónico que terminen en ”@example.org”.
db.posts.delete_many({'user_email': {'$regex': '@example\.org$'}})

DeleteResult({'n': 815, 'ok': 1.0}, acknowledged=True)

7. Indexación y optimización avanzadas

In [167]:
# 1. Crear un índice en el campo ”user_email” para búsquedas de correo electrónico más rápidas.
db.posts.create_index([('user_email', 1)])

'user_email_1'

In [23]:
# 2. Explicar el plan de consulta para encontrar usuarios con edad mayor a 30.
list(db.posts.find({'user_age': {'$gt': 30}}, {'user': 1, 'user_age': 1, '_id': 0}).explain())
 

['explainVersion',
 'queryPlanner',
 'executionStats',
 'command',
 'serverInfo',
 'serverParameters',
 'ok']

# 3. Discutir las ventajas y desventajas de almacenar comentarios dentro del documento de usuario<br>

Ventajas:<br>
- Mejoras en el rendimiento: al almacenar los comentarios dentro de la publicación, se obtendrán los comentarios de cada publicación mucho más rápido para ser mostrados al usuario. No habrá necesidad de realizar múltiples y/o extensas consultas. Con una sola consulta será suficiente, lo que mejora el rendimiento del sistema.<br>
- Facilidad de acceso a comentarios: el acceso a los comentarios de cada publicación es más sencillo, simplemente con un comments.comment se accede a cada comentario de la publicación. Lo convierte en más intuitivo para el programador.<br>
- Mayor agilidad en cambios: para realizar cambios ayuda bastante porque no habría que realizar un consulta grande para modificar o eliminar un comentario de una publicación específica.<br>

Desventajas:<br>
- Tamaño del documento: el tamaño del documento aumenta mucho al almacenar todos sus comentarios, lo que hará que el sistema necesite mayor capacidad para transmitir, almacenar y procesar los datos, tanto de red como de base de datos y hardware.<br>
- Dificultad en ciertas consultas: ciertas consultas pueden ser muy complejas o costosas debido a la estrutura anteriormente planteada.<br>
- Problemas de concurencia: si dos comentarios diferentes de la misma publicación necesitan ser actualizados, puede generar conflictos que afecten al documento.